In [17]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
from sklearn.metrics import r2_score
from sklearn.model_selection import train_test_split

def ts_train_test_split(X,y,test_size=0.35,random_state=42, shuffle=True, filtre = True, limite = 0):
    Xtemp, ytemp = X.copy(), y.copy()
    a= X.index - X.index[0]
    a= a.days
    Xtemp['id']=a
    ytemp['id']=a
    from sklearn.model_selection import train_test_split
    indices_train, indices_test=train_test_split(a.unique(), test_size=test_size,random_state=random_state, shuffle=shuffle)
    X_train = Xtemp[Xtemp['id'].isin(indices_train.values)]
    X_test = Xtemp[Xtemp['id'].isin(indices_test.values)]
    y_train = ytemp[ytemp['id'].isin(indices_train.values)]
    y_test = ytemp[ytemp['id'].isin(indices_test.values)]
    ####
    if filtre:
        c=y_test.groupby('id').max()>limite
        X_test = X_test.loc[y_test['id'].isin(c.index[c["elecWithoutEclairage"]])]
        y_test = y_test.loc[y_test['id'].isin(c.index[c["elecWithoutEclairage"]])]


    X_train = X_train.drop(["id"], axis=1)
    X_test = X_test.drop(["id"], axis=1)
    y_train = y_train.drop(["id"], axis=1)
    y_test = y_test.drop(["id"], axis=1)
    # print(y_test)
    
    
    return X_train, X_test, y_train, y_test

y=pd.read_csv("y_selected.csv", parse_dates=["date"], index_col="date")
X=pd.read_csv("A_dataComplet.csv", parse_dates=["date"], index_col="date")        
X_train, X_test, y_train, y_test = ts_train_test_split(X,y,test_size=0.20,random_state=0, shuffle=True)
rfr = RandomForestRegressor(n_estimators = 100,oob_score = True,n_jobs = -1, max_depth=10,max_features=0.33,min_samples_leaf=30)
#y_train=y_train.values.ravel()
rfr.fit(X_train, y_train.values.ravel())
score = rfr.score(X_train, y_train.values.ravel())
# print("R-squared:", score) 
y_predTest = rfr.predict(X_test)
y_predTrain = rfr.predict(X_train)
rmseTest = mean_squared_error(y_test, y_predTest,squared=False)
rmseTrain = mean_squared_error(y_train, y_predTrain,squared=False)
print(rmseTrain,";",rmseTest)

58.57634720156094 ; 104.7411831587254


In [21]:
fn=X.columns.values
cn=y.columns.values
fig, axes = plt.subplots(nrows = 1,ncols = 1,figsize = (16,16), dpi=1800)
tree.plot_tree(rfr.estimators_[0],
               feature_names = fn, 
               class_names=cn,
               filled = True);
fig.savefig('rf_individualtree2.png')

In [4]:
data.feature_names

array(['mean radius', 'mean texture', 'mean perimeter', 'mean area',
       'mean smoothness', 'mean compactness', 'mean concavity',
       'mean concave points', 'mean symmetry', 'mean fractal dimension',
       'radius error', 'texture error', 'perimeter error', 'area error',
       'smoothness error', 'compactness error', 'concavity error',
       'concave points error', 'symmetry error',
       'fractal dimension error', 'worst radius', 'worst texture',
       'worst perimeter', 'worst area', 'worst smoothness',
       'worst compactness', 'worst concavity', 'worst concave points',
       'worst symmetry', 'worst fractal dimension'], dtype='<U23')

In [8]:
y.columns.values

array(['elecWithoutEclairage'], dtype=object)

In [50]:
y.max()

elecWithoutEclairage    1639.796
dtype: float64

In [54]:
power = 200
print("power;taux")
while (power< y['elecWithoutEclairage'].max()):
    power = power + 50
    taux = (y["elecWithoutEclairage"]>power).sum()/y.shape[0]*100
    print(power,";", taux)
    


power;taux
250 ; 97.74080086580086
300 ; 78.53986291486291
350 ; 14.127886002886003
400 ; 10.547438672438672
450 ; 8.125901875901874
500 ; 6.885822510822511
550 ; 5.830627705627705
600 ; 4.95580808080808
650 ; 4.2523448773448775
700 ; 3.7337662337662336
750 ; 3.242243867243867
800 ; 2.701118326118326
850 ; 2.0427489177489178
900 ; 1.618867243867244
950 ; 1.1408730158730158
1000 ; 0.8522727272727272
1050 ; 0.4825036075036075
1100 ; 0.27056277056277056
1150 ; 0.15331890331890333
1200 ; 0.07665945165945166
1250 ; 0.05411255411255411
1300 ; 0.040584415584415584
1350 ; 0.027056277056277056
1400 ; 0.018037518037518036
1450 ; 0.018037518037518036
1500 ; 0.013528138528138528
1550 ; 0.009018759018759018
1600 ; 0.009018759018759018
1650 ; 0.0


In [41]:
(X["co2_100"]>550).sum()/y.shape[0]

0.14574314574314573

In [58]:
co2 = 400
print("co2 en ppm;taux")
while (co2< X["co2_100"].max()):
    co2 = co2 + 50
    taux = (X["co2_100"]>co2).sum()/y.shape[0]*100
    print(co2,";", taux)

co2 en ppm;taux
450 ; 27.827380952380953
500 ; 18.790584415584416
550 ; 14.574314574314574
600 ; 11.828102453102453
650 ; 9.816919191919192
700 ; 8.342352092352092
750 ; 7.242063492063493
800 ; 6.322150072150072
850 ; 5.523989898989899
900 ; 4.797979797979798
950 ; 4.261363636363636
1000 ; 3.796897546897547
1050 ; 3.3775252525252526
1100 ; 2.876984126984127
1150 ; 2.5432900432900434
1200 ; 2.241161616161616
1250 ; 1.948051948051948
1300 ; 1.7135642135642135
1350 ; 1.488095238095238
1400 ; 1.2671356421356421
1450 ; 1.077741702741703
1500 ; 0.9063852813852814
1550 ; 0.7620851370851371
1600 ; 0.5997474747474747
1650 ; 0.468975468975469
1700 ; 0.31565656565656564
1750 ; 0.13528138528138528
1800 ; 0.06764069264069264
1850 ; 0.040584415584415584
1900 ; 0.03607503607503607
1950 ; 0.03156565656565657
2000 ; 0.022546897546897548
2050 ; 0.018037518037518036
2100 ; 0.018037518037518036
2150 ; 0.018037518037518036
2200 ; 0.013528138528138528
2250 ; 0.009018759018759018
2300 ; 0.004509379509379509
